# P1 circuit 4 qubits 

In [15]:
import pennylane as qml
import numpy as np
# Path to your QASM file
qasm_path = "circuit_qasm/P1_little_peak.qasm"
number_of_qubits = 4
# Load the circuit from QASM
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# Create a device matching the number of qubits (adjust wires as needed)
dev = qml.device("default.qubit", wires=number_of_qubits,shots=1000)

# Convert QASM string to a PennyLane circuit
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.probs()

# Run the circuit
state = run_circuit()
print(state)
print(qml.draw(circuit)())
max_index = np.argmax(state)
print(max_index)
print(format(max_index, f'0{number_of_qubits}b'))

[0.006 0.069 0.    0.006 0.001 0.008 0.    0.001 0.085 0.642 0.005 0.068
 0.011 0.093 0.001 0.004]
0: ──RY(2.51)───────────┤  
1: ──X─────────RY(2.51)─┤  
2: ──X─────────RY(2.51)─┤  
3: ──RY(2.51)───────────┤  
9
1001


# P2 circuit 28 qubits

In [27]:
%pip install python-dotenv
%pip install bluequbit

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [25]:
from dotenv import load_dotenv
import os

load_dotenv() 

token = os.getenv("TOKEN")

In [45]:
import pennylane as qml
import numpy as np
import os
import json
from collections import Counter

# --- Config ---
qasm_path = "circuit_qasm/P2_swift_rise.qasm"
number_of_qubits = 28
shots = 1000
json_path = "resultsP2.json"

# --- Load QASM ---
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# --- Setup Device and Circuit ---
dev = qml.device("bluequbit.cpu", wires=number_of_qubits, token=token, shots=shots)
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.sample()

# --- Run the Circuit ---
state = run_circuit()
print(state)
print(qml.draw(circuit)())

# --- Convert Samples to Bitstrings ---
bitstrings = ["".join(map(str, s)) for s in state]  # Each sample to string
bitstring_counts = Counter(bitstrings)

# --- Update resultsP2.json ---
# Load old data if exists
if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in bitstring_counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")


[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


[BQ-PYTHON-SDK][INFO] - Submitted: Job ID: XRP5B8jx2uKTr3eg, device: pennylane.cpu, run status: RUNNING, created on: 2025-04-12 19:19:37 UTC, estimated runtime: 116300 ms, estimated cost: $0.00, num qubits: 28
Job ID: XRP5B8jx2uKTr3eg, device: pennylane.cpu, run status: COMPLETED, created on: 2025-04-12 19:19:37 UTC, cost: $0.00, run time: 73162 ms, queue time: 153 ms, num qubits: 28
[[1 1 0 ... 1 0 0]
 [1 1 0 ... 1 0 0]
 [1 1 0 ... 0 1 0]
 ...
 [1 1 0 ... 1 0 0]
 [1 1 0 ... 1 0 0]
 [0 0 0 ... 1 0 0]]
 0: ──RZ(-0.48)──SX──RZ(-1.05)──SX──RZ(-2.62)─╭Z──RZ(-1.56)──SX──RZ(-1.49)──SX──RZ(2.69)─────╭●
 1: ──RZ(-0.93)──SX──RZ(-0.39)──SX──RZ(2.32)──╰●──RZ(-0.35)──SX──RZ(-2.86)──SX──RZ(-0.50)─╭Z─│─
 2: ──RZ(-1.50)──SX──RZ(-2.24)──SX──RZ(-1.20)─╭Z──RZ(1.67)───SX──RZ(-1.50)──SX──RZ(-2.07)─╰●─│─
 3: ──RZ(3.05)───SX──RZ(-0.79)──SX──RZ(1.08)──╰●──RZ(0.56)───SX──RZ(-1.34)──SX──RZ(-1.79)─╭Z─│─
 4: ──RZ(2.23)───SX──RZ(-1.81)──SX──RZ(-2.12)─╭Z──RZ(0.08)───SX──RZ(-0.98)──SX──RZ(0.49)──╰●─│─
 5: ──RZ(1.49

In [48]:
import json

json_path = "resultsP2.json"

# Load the JSON data
with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")


🔝 Top 5 most common bitstrings with probabilities:
0011100001101100011011010011 → 353 times (0.3495 probability)
1011100001101100011011011010 → 5 times (0.0050 probability)
0011011101101100011011010011 → 5 times (0.0050 probability)
0011100000110100011011010011 → 4 times (0.0040 probability)
0011111101101100011011010011 → 4 times (0.0040 probability)


# P3

In [53]:
import pennylane as qml
import numpy as np
import os
import json
from collections import Counter

# --- Config ---
qasm_path = "circuit_qasm/P3__sharp_peak.qasm"
number_of_qubits = 44
shots = 1000
json_path = "resultsP3.json"

# --- Load QASM ---
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# --- Setup Device and Circuit ---
dev = qml.device("bluequbit.cpu", wires=number_of_qubits, token=token, shots=shots)
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.sample()

# --- Run the Circuit ---
state = run_circuit()
print(state)
print(qml.draw(circuit)())

# --- Convert Samples to Bitstrings ---
bitstrings = ["".join(map(str, s)) for s in state]  # Each sample to string
bitstring_counts = Counter(bitstrings)

# --- Update resultsP2.json ---
# Load old data if exists
if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in bitstring_counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")


[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


BQJobNotCompleteError: Job pVHIEGtC3BMIqEcz finished with status: FAILED_VALIDATION. Circuit contains more than 33 qubits, which is not supported for CPU backend with Pennylane. See https://app.bluequbit.io/docs for more details.

In [ ]:
import json

json_path = "resultsP3.json"

# Load the JSON data
with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")


### qiskit

In [ ]:
from qiskit import transpile
from qiskit.visualization import plot_histogram
from qiskit import qasm2
from collections import Counter
import json
import bluequbit

# --- Config ---
qasm_path = "circuit_qasm/P3__sharp_peak.qasm"
json_path = "resultsP3.json"
shots = 1000
device = "mps.cpu"  # or "cpu", "gpu", "quantum"

# --- Init BlueQubit ---
bq = bluequbit.init(token)

# --- Load QASM ---
circuit = qasm2.load(qasm_path)

# Ensure measurement if not present
if not circuit.cregs:
    circuit.measure_all()

# --- Run on BlueQubit ---
results = bq.run(
    circuits=circuit,
    device=device,
    shots=shots,
    asynchronous=False,
    job_name="sharp-peak-qasm"
    )

# --- Get Results ---
counts = results.get_counts()

# --- Output ---

# Save to JSON
with open(json_path, "w") as f:
    json.dump(counts, f, indent=2)

if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")

with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")



[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


[BQ-PYTHON-SDK][INFO] - Submitted: Job ID: Nr0N7dmoiJdDmWzA, name: sharp-peak-qasm, device: mps.cpu, run status: RUNNING, created on: 2025-04-12 21:20:49 UTC, estimated runtime: 100 ms, estimated cost: $0.00, num qubits: 44
Top measurement results:
10001101010101010000011111001101000100011010 => 107 (10.70%)
10001101010100100000011111001101000100011010 => 24 (2.40%)
10001101010101010001101111001101000100011010 => 12 (1.20%)
10001101010101010001010111001101000100011010 => 10 (1.00%)
10001101010101010000001111001101000100011010 => 7 (0.70%)
✅ All results saved and updated.
🔝 Top 5 most common bitstrings with probabilities:
0011100001101100011011010011 → 349 times (0.1745 probability)
01011000100010110011111000001010101010110001 → 107 times (0.0535 probability)
01011000100010110011111000000100101010110001 → 24 times (0.0120 probability)
01011000100010110011110110001010101010110001 → 12 times (0.0060 probability)
01011000100010110011101010001010101010110001 → 10 times (0.0050 probability)


# P4

drawing in pennylane

In [68]:
import pennylane as qml
import numpy as np
# Path to your QASM file
qasm_path = "circuit_qasm/P4_golden_mountain.qasm"
number_of_qubits = 4
# Load the circuit from QASM
with open(qasm_path, "r") as f:
    qasm_str = f.read()

# Create a device matching the number of qubits (adjust wires as needed)
dev = qml.device("default.qubit", wires=number_of_qubits,shots=1000)

# Convert QASM string to a PennyLane circuit
circuit = qml.from_qasm(qasm_str)

@qml.qnode(dev)
def run_circuit():
    circuit()
    return qml.probs()

print(qml.draw(circuit)())


 0: ──U3(2.01,-0.88,1.80)──╭●──U3(2.47,0.00,-1.57)─╭●──U3(0.10,2.42,-3.11)─────────────────────────
 1: ──U3(1.10,2.52,-2.25)──╰Z──U3(0.90,0.00,1.57)──╰Z──U3(2.08,-0.24,-0.55)─╭●──U3(3.00,0.00,-1.57)
 2: ──U3(2.01,-1.19,2.94)──╭●──U3(3.05,0.00,-1.57)─╭●──U3(0.20,-0.78,-2.27)─╰Z──U3(1.19,0.00,1.57)─
 3: ──U3(1.56,3.04,-1.80)──╰Z──U3(0.13,0.00,1.57)──╰Z──U3(1.64,0.60,-2.05)──╭●──U3(3.00,0.00,-1.57)
 4: ──U3(1.45,2.52,-0.71)──╭●──U3(2.97,0.00,-1.57)─╭●──U3(1.54,2.33,2.10)───╰Z──U3(1.07,0.00,1.57)─
 5: ──U3(0.93,-1.19,-2.51)─╰Z──U3(1.45,0.00,1.57)──╰Z──U3(1.01,-2.99,1.45)──╭●──U3(3.03,0.00,-1.57)
 6: ──U3(3.08,-0.51,-1.25)─╭●──U3(1.97,0.00,-1.57)─╭●──U3(2.18,-2.30,1.94)──╰Z──U3(0.55,0.00,1.57)─
 7: ──U3(0.00,2.13,2.19)───╰Z──U3(1.27,0.00,1.57)──╰Z──U3(1.59,-0.33,-2.22)─╭●──U3(2.17,0.00,-1.57)
 8: ──U3(1.26,-1.51,-0.67)─╭●──U3(2.09,0.00,-1.57)─╭●──U3(1.41,-1.73,2.58)──╰Z──U3(1.30,0.00,1.57)─
 9: ──U3(0.10,-3.03,1.97)──╰Z──U3(1.46,0.00,1.57)──╰Z──U3(1.86,-0.56,2.47)──╭●──U3(3.13,0.00,-1.57)


In [ ]:
from qiskit import transpile
from qiskit.visualization import plot_histogram
from qiskit import qasm2
from collections import Counter
import json
import bluequbit

# --- Config ---
qasm_path = "circuit_qasm/P4_golden_mountain.qasm"
json_path = "resultsP4.json"
shots = 1000
device = "mps.cpu"  # or "cpu", "gpu", "quantum"

# --- Init BlueQubit ---
bq = bluequbit.init(token)

# --- Load QASM ---
circuit = qasm2.load(qasm_path)

# Ensure measurement if not present
if not circuit.cregs:
    circuit.measure_all()

# --- Run on BlueQubit ---
results = bq.run(
    circuits=circuit,
    device=device,
    shots=shots,
    asynchronous=False,
    job_name="sharp-peak-qasm",
    options={'mps_bond_dimension':128,'mps_truncation_threshold':1e-16}
    )

# --- Get Results ---
counts = results.get_counts()

# --- Output ---

# Save to JSON
with open(json_path, "w") as f:
    json.dump(counts, f, indent=2)

if os.path.exists(json_path):
    with open(json_path, "r") as f:
        old_counts = json.load(f)
else:
    old_counts = {}

# Merge new counts
for k, v in counts.items():
    old_counts[k] = old_counts.get(k, 0) + v

# Save updated results
with open(json_path, "w") as f:
    json.dump(old_counts, f, indent=4)

print("✅ All results saved and updated.")

with open(json_path, "r") as f:
    result_counts = json.load(f)

# Total number of samples
total_counts = sum(result_counts.values())

# Sort by frequency (value), descending
sorted_results = sorted(result_counts.items(), key=lambda x: x[1], reverse=True)

# Display top 5 with probability
print("🔝 Top 5 most common bitstrings with probabilities:")
for bitstring, count in sorted_results[:5]:
    probability = count / total_counts
    print(f"{bitstring[::-1]} → {count} times ({probability:.4f} probability)")

[BQ-PYTHON-SDK][WARNING] - Beta version 0.12.0b1 of BlueQubit Python SDK is being used.


BQJobNotCompleteError: Job 7vcPvgxyz02sdZH4 finished with status: FAILED_VALIDATION. The number of two-qubit gates is too big for mps.cpu (maximum 1000). See https://app.bluequbit.io/docs for more details.

In [78]:
two_qubit_gates = [gate for gate, qargs, _ in qc.data if len(qargs) == 2]
print("Number of 2-qubit gates:", len(two_qubit_gates))

Number of 2-qubit gates: 210


C:\Users\Kuift\AppData\Local\Temp\ipykernel_8620\1035872585.py:1: DeprecationWarning: Treating CircuitInstruction as an iterable is deprecated legacy behavior since Qiskit 1.2, and will be removed in Qiskit 2.0. Instead, use the `operation`, `qubits` and `clbits` named attributes.
  two_qubit_gates = [gate for gate, qargs, _ in qc.data if len(qargs) == 2]
